In [1]:
import ast
import csv
import json
import glom

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn2_circles

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

pd.set_option('display.max_columns', None)

In [2]:
with open('../data/raw/fairsharing_dump_api_09_2021.json') as f:
    lines = f.read().splitlines()
    
fairsharing_df = pd.DataFrame(lines)
fairsharing_df.columns = ['json_element']
fairsharing_df['json_element'].apply(json.loads)
fairsharing_df = pd.json_normalize(fairsharing_df['json_element'].apply(json.loads))

fairsharing_df['unique_id'] = 'FAIRsharing_' + fairsharing_df.id
fairsharing_df = fairsharing_df.add_prefix('FAIRsharing_')
fairsharing_df.head()

FAIRsharing_id     FAIRsharing_type FAIRsharing_attributes.created-at  \
0           1723  fairsharing-records          2014-11-04T15:23:40.000Z   
1           3101  fairsharing-records          2020-09-16T08:49:13.000Z   
2           2649  fairsharing-records          2018-08-07T20:23:32.000Z   
3           2657  fairsharing-records          2018-08-13T15:12:11.000Z   
4           2078  fairsharing-records          2014-11-04T15:23:40.000Z   

  FAIRsharing_attributes.updated-at FAIRsharing_attributes.metadata.doi  \
0          2021-09-30T11:39:06.829Z         10.25504/FAIRsharing.8t18te   
1          2021-09-30T11:36:45.452Z                                 NaN   
2          2021-09-30T11:39:07.898Z                                 NaN   
3          2021-09-30T11:37:28.736Z         10.25504/FAIRsharing.tnByoG   
4          2021-09-30T11:34:43.129Z         10.25504/FAIRsharing.3axym7   

       FAIRsharing_attributes.metadata.name  \
0                        Cell Image Library   
1             WHOI Ship Data-Grabber System   
2  Electron Microscope Public Image Archive   
3              ClinicalStudyDataRequest.com   
4   Germplasm Resources Information Network   

  FAIRsharing_attributes.metadata.status  \
0                                  ready   
1                                  ready   
2                                  ready   
3                                  ready   
4                                  ready   

            FAIRsharing_attributes.metadata.contacts  \
0  [{'contact-name': 'David Orloff', 'contact-ema...   
1                                                NaN   
2  [{'contact-name': 'General contact', 'contact-...   
3  [{'contact-email': 'support@clinicalstudydatar...   
4           [{'contact-email': 'dbmu@ars-grin.gov'}]   

           FAIRsharing_attributes.metadata.homepage  \
0                   http://www.cellimagelibrary.org   
1  http://4dgeo.whoi.edu/shipdata/SDG_shipdata.html   
2           https://www.ebi.ac.uk/pdbe/emdb/empiar/   
3             https://clinicalstudydatarequest.com/   
4                         https://www.ars-grin.gov/   

   FAIRsharing_attributes.metadata.identifier  \
0                                        1723   
1                                        3101   
2                                        2649   
3                                        2657   
4                                        2078   

         FAIRsharing_attributes.metadata.description  \
0  This library is a public and easily accessible...   
1  The WHOI Ship DataGrabber system provides the ...   
2  EMPIAR, the Electron Microscopy Public Image A...   
3  ClinicalStudyDataRequest.com (CSDR) is a conso...   
4  GRIN provides National Genetic Resources Progr...   

       FAIRsharing_attributes.metadata.support-links  \
0  [{'url': 'http://www.cellimagelibrary.org/page...   
1  [{'url': 'http://4dgeo.whoi.edu/shipdata/SDG_o...   
2  [{'url': 'https://www.ebi.ac.uk/support/EMPIAR...   
3  [{'url': 'https://clinicalstudydatarequest.com...   
4  [{'url': 'https://www.ars-grin.gov/Pages/Colle...   

   FAIRsharing_attributes.metadata.year-creation  \
0                                         2010.0   
1                                         2004.0   
2                                         2015.0   
3                                         2014.0   
4                                         2010.0   

      FAIRsharing_attributes.metadata.data-processes  \
0  [{'name': 'live update', 'type': 'data release...   
1  [{'url': 'http://4dgeo.whoi.edu/sdg-bin/dv_mai...   
2  [{'url': 'https://www.ebi.ac.uk/pdbe/emdb/empi...   
3  [{'url': 'https://clinicalstudydatarequest.com...   
4  [{'url': 'https://www.ars-grin.gov/', 'name': ...   

  FAIRsharing_attributes.legacy-ids  \
0   [biodbcore-000180, bsg-d000180]   
1   [biodbcore-001609, bsg-d001609]   
2   [biodbcore-001140, bsg-d001140]   
3   [biodbcore-001149, bsg-d001149]   
4   [biodbcore-000546, bsg-d000546]   

  FAIRsharing_attributes.fairs

In [3]:
re3data_df = pd.read_csv('../data/raw/re3data.tsv', delimiter='\t',
                        converters={'subject': ast.literal_eval,
                                    'keyword': ast.literal_eval,
                                    'additionalName': ast.literal_eval,
                                    'repositoryIdentifier': ast.literal_eval,
                                    'type': ast.literal_eval,
                                    'contentType': ast.literal_eval,
                                    'providerType': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })

re3data_df['unique_id'] = 're3data_' + re3data_df.orgIdentifier
re3data_df = re3data_df.add_prefix('re3data_')
re3data_df.head()

re3data_OpenAIREID re3data_orgIdentifier  \
0  re3data_____::91780fe96da5ba32f804e43359c154ba          r3d100000001   
1  re3data_____::cc3ea05c863cd49af75f7f54e0e86f09          r3d100000002   
2  re3data_____::a2f73fbe91311f4356d0d7957c441773          r3d100000004   
3  re3data_____::0394b97eb11f19785cbca1ec830429da          r3d100000005   
4  re3data_____::a48f09c562b247a9919acfe195549b47          r3d100000006   

             re3data_repositoryName  \
0  Odum Institute Archive Dataverse   
1      Access to Archival Databases   
2    Datenbank Gesprochenes Deutsch   
3                     UNC Dataverse   
4          Archaeology Data Service   

                              re3data_additionalName  \
0                                                 []   
1                                              [AAD]   
2  [DGD, DGD2 (formerly), Database for Spoken Ger...   
3           [University of North Carolina Dataverse]   
4                                              [ADS]   

                      re3data_repositoryURL  \
0  https://dataverse.unc.edu/dataverse/odum   
1             https://aad.archives.gov/aad/   
2              https://dgd.ids-mannheim.de/   
3                https://dataverse.unc.edu/   
4     https://archaeologydataservice.ac.uk/   

                    re3data_repositoryIdentifier  \
0                                             []   
1             [RRID:SCR_010479, RRID:nlx_157752]   
2                                             []   
3                                             []   
4  [FAIRsharing_doi:10.25504/FAIRsharing.hm1mfg]   

                                 re3data_description     re3data_type  \
0  The Odum Institute Archive Dataverse contains ...   [disciplinary]   
1  You will find in the Access to Archival Databa...   [disciplinary]   
2  The "Database for Spoken German (DGD)" is a co...   [disciplinary]   
3  UNC Dataverse is an open-source repository sof...  [institutional]   
4  The ADS is an accredited digital repository fo...   [disciplinary]   

                                    re3data_size re3data_updateDate  \
0                  13 dataverses; 3.050 datasets         2020-12-04   
1                                            NaN                NaN   
2                                     34 corpora         2020-02-03   
3  186 dataverses; 25.272 studies; 229.442 files         2020-11-30   
4                                   1837 results         2020-05-20   

  re3data_startDate re3data_endDate  \
0               NaN             NaN   
1              1985             NaN   
2              2012             NaN   
3              2011             NaN   
4        1996-10-01             NaN   

                                     re3data_subject  \
0  [1 Humanities and Social Sciences, 111 Social ...   
1  [1 Humanities and Social Sciences, 102 History...   
2  [1 Humanities and Social Sciences, 104 Linguis...   
3  [1 Humanities and Social Sciences, 111 Social ...   
4  [1 Humanities and Social Sciences, 101 Ancient...   

   re3data_missionStatement  \
0                     False   
1                      True   
2                      True   
3                      True   
4                      True   

                                 re3data_contentType  \
0  [Databases, Plain text, Scientific and statist...   
1  [Images, Standard office documents, Structured...   
2  [Audiovisual data, Standard office documents, ...   
3  [Archived data, Plain text, Raw data, Scientif...   
4  [Archived data, Audiovisual data, Databases, I...   

              re3data_providerType  \
0                   [dataProvider]   
1                   [dataProvider]   
2  [dataProvider, serviceProvider]   
3  [dataProvider, serviceProvider]   
4  [dataProvider, serviceProvider]   

                                     re3data_keyword  \
0  [FAIR, Middle East, crime, demography, economy...   
1                                       [US History]   
2  [Australian German, FOLK, German dialects, Pfe... 

In [4]:
opendoar_df = pd.read_csv('../data/raw/openDoar.tsv', delimiter='\t',
                         converters={'subject': ast.literal_eval,
                                    'alternativeNames': ast.literal_eval,
                                    'contentType': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    },
                         dtype={'orgIdentifier': str})

opendoar_df['unique_id'] = 'OpenDOAR_' + opendoar_df.orgIdentifier
opendoar_df = opendoar_df.add_prefix('OpenDOAR_')
opendoar_df.head()

OpenDOAR_OpenAIREID OpenDOAR_orgIdentifier  \
0  opendoar____::82161242827b703e6acf9c726942a1e4                    175   
1  opendoar____::ea5d2f1c4608232e07d3aa3d998e5135                     64   
2  opendoar____::a8f15eda80c50adb0e71943adc8015cf                    151   
3  opendoar____::65b9eea6e1cc6bb9f0cd2a47751a186f                    105   
4  opendoar____::38b3eff8baf56627478ec76a704e9b52                    101   

                             OpenDOAR_repositoryName  \
0                                  hku theses online   
1  research support scheme - central european uni...   
2                    cadmus, eui research repository   
3                           document server@uhasselt   
4                      utrecht university repository   

  OpenDOAR_alternativeNames               OpenDOAR_repositoryURL  \
0                        []  http://hub.hku.hk/handle/10722/1057   
1                        []          http://rss.archives.ceu.hu/   
2                        []                http://cadmus.eui.eu/   
3                        []   https://doclib.uhasselt.be/dspace/   
4                        []          http://dspace.library.uu.nl   

                                OpenDOAR_description  OpenDOAR_type  \
0  this is an institutional repository providing ...  institutional   
1  this is an institutional repository collecting...  institutional   
2  cadmus is the name of the eui research reposit...  institutional   
3  this site is a university repository providing...  institutional   
4  this site is a university repository providing...  institutional   

   OpenDOAR_updateDate   OpenDOAR_startDate  \
0  2021-03-25 10:16:18  2005-12-21 12:44:08   
1  2021-03-25 09:48:31  2006-01-04 14:59:30   
2  2021-09-13 13:35:36  2006-01-04 12:07:07   
3  2021-04-16 15:23:52  2006-01-24 15:46:44   
4  2021-04-16 15:22:03  2006-01-13 12:55:13   

                                    OpenDOAR_subject  \
0                                [multidisciplinary]   
1                                [multidisciplinary]   
2  [history and archaeology, multidisciplinary, s...   
3                                [multidisciplinary]   
4                                [multidisciplinary]   

                                OpenDOAR_contentType  \
0  [bibliographic_references, theses_and_disserta...   
1                 [unpub_reports_and_working_papers]   
2  [journal_articles, theses_and_dissertations, u...   
3  [journal_articles, conference_and_workshop_pap...   
4  [journal_articles, conference_and_workshop_pap...   

                                OpenDOAR_institution  OpenDOAR_metadataPolicy  \
0  [[university of hong kong, [香港大學, hku], cn, ht...                    False   
1  [[central european university, [ceu], hu, http...                    False   
2  [[european university institute, [eui], it, ht...                    False   
3  [[hasselt university, [universiteit hasselt, u...                    False   
4  [[university of utrecht, [universiteit utrecht...                    False   

   OpenDOAR_dataPolicy  OpenDOAR_submissionPolicy  OpenDOAR_contentPolicy  \
0                False                      False                   False   
1                False                      False                   False   
2                False                      False                   False   
3                False                      False                   False   
4                False                      False                   False   

            OpenDOAR_software OpenDOAR_api OpenDOAR_unique_id  
0  dspace cris-5.3.1-snapshot       false        OpenDOAR_175  
1               eprints 2.2.1        true         OpenDOAR_64  
2                  dspace 5.2        true        OpenDOAR_151  
3                dspace 1.7.2        true        OpenDOAR_105  
4                     dspace         true        OpenDOAR_101

In [5]:
roar_df = pd.read_csv('../data/raw/export_roar_CSV.csv', dtype='str')
roar_df = roar_df.groupby('eprintid').aggregate(set)

def value_or_list(cell_set):
    copy = set(cell_set)
    copy.discard(np.nan) 
    if len(copy) == 0:
        return np.nan
    if len(copy) == 1:
        return copy.pop()
    return list(copy)
        
roar_df = roar_df.applymap(value_or_list)
roar_df.reset_index(inplace=True)

roar_df['unique_id'] = 'roar_' + roar_df.eprintid
roar_df = roar_df.add_prefix('roar_')
roar_df.head()

roar_eprintid roar_rev_number roar_eprint_status roar_userid  roar_importid  \
0             1             633            archive           1            NaN   
1            10             511            archive           1            NaN   
2          1000             274            archive           1            NaN   
3         10001              20            archive          91            NaN   
4         10008              11            archive         404            NaN   

   roar_source           roar_dir       roar_datestamp         roar_lastmod  \
0          NaN  disk0/00/00/00/01  2010-01-06 13:43:48  2011-07-18 05:40:07   
1          NaN  disk0/00/00/00/10  2010-01-06 13:43:48  2011-07-18 05:40:13   
2          NaN  disk0/00/00/10/00  2010-01-06 13:45:01  2011-07-06 08:21:21   
3          NaN  disk0/00/01/00/01  2015-08-08 14:52:11  2016-03-21 19:44:01   
4          NaN  disk0/00/01/00/08  2015-08-08 14:52:26  2016-03-21 19:43:51   

   roar_status_changed      roar_type roar_succeeds  roar_commentary  \
0  2010-01-06 13:43:48        subject           NaN              NaN   
1  2010-01-06 13:43:48  institutional           NaN              NaN   
2  2010-01-06 13:45:01        subject           NaN              NaN   
3  2015-08-08 14:52:11        subject           NaN              NaN   
4  2015-08-08 14:52:26  institutional           NaN              NaN   

  roar_metadata_visibility  roar_latitude  roar_longitude  roar_relation_type  \
0                     show            NaN             NaN                 NaN   
1                     show            NaN             NaN                 NaN   
2                     show            NaN             NaN                 NaN   
3                     show            NaN             NaN                 NaN   
4                     show            NaN             NaN                 NaN   

   roar_relation_uri roar_item_issues_id roar_item_issues_type  \
0                NaN                 NaN                   NaN   
1                NaN                 NaN                   NaN   
2                NaN                 NaN                   NaN   
3                NaN                 NaN                   NaN   
4                NaN                 NaN                   NaN   

  roar_item_issues_description roar_item_issues_timestamp  \
0                          NaN                        NaN   
1                          NaN                        NaN   
2                          NaN                        NaN   
3                          NaN                        NaN   
4                          NaN                        NaN   

  roar_item_issues_status  roar_item_issues_reported_by  \
0                     NaN                           NaN   
1                     NaN                           NaN   
2                     NaN                           NaN   
3                     NaN                           NaN   
4                     NaN                           NaN   

   roar_item_issues_resolved_by  roar_item_issues_comment  \
0                           NaN                       NaN   
1                           NaN                       NaN   
2                           NaN                       NaN   
3                           NaN                       NaN   
4                           NaN                       NaN   

  roar_item_issues_count  roar_sword_depositor  roar_sword_slug roar_exemplar  \
0                      0                   NaN              NaN           NaN   
1                      0                   NaN              NaN           NaN   
2                      0                   NaN              NaN           NaN   
3                    NaN                   NaN              NaN           NaN   
4                    NaN                   NaN              NaN           NaN   

                                roar_home_page  \
0              http://archivesic.ccsd.cnrs.fr/   
1              http://www.diva-portal.org/mdh/ 

In [6]:
roar_df[roar_df.roar_eprintid == '10013']

roar_eprintid roar_rev_number roar_eprint_status roar_userid  roar_importid  \
7         10013              31            archive        7104            NaN   

   roar_source           roar_dir       roar_datestamp         roar_lastmod  \
7          NaN  disk0/00/01/00/13  2015-08-08 14:53:04  2016-03-21 19:54:43   

   roar_status_changed      roar_type roar_succeeds  roar_commentary  \
7  2015-08-08 14:53:04  institutional           NaN              NaN   

  roar_metadata_visibility  roar_latitude  roar_longitude  roar_relation_type  \
7                     show            NaN             NaN                 NaN   

   roar_relation_uri roar_item_issues_id roar_item_issues_type  \
7                NaN                 NaN                   NaN   

  roar_item_issues_description roar_item_issues_timestamp  \
7                          NaN                        NaN   

  roar_item_issues_status  roar_item_issues_reported_by  \
7                     NaN                           NaN   

   roar_item_issues_resolved_by  roar_item_issues_comment  \
7                           NaN                       NaN   

  roar_item_issues_count  roar_sword_depositor  roar_sword_slug roar_exemplar  \
7                    NaN                   NaN              NaN           NaN   

          roar_home_page                                         roar_title  \
7  http://er.ucu.edu.ua/  ErUCU: Electronic repository of the Ukrainian ...   

                       roar_oai_pmh          roar_sword_endpoint  \
7  http://er.ucu.edu.ua/oai/request  http://er.ucu.edu.ua/sword/   

                            roar_rss_feed roar_twitter_feed  \
7  http://er.ucu.edu.ua/feed/rss_2.0/site               NaN   

                                    roar_description roar_fulltext  \
7  Ukrainian Catholic University’s institutional ...          TRUE   

  roar_open_access roar_mandate        roar_organisation_title  \
7             TRUE         TRUE  Ukrainian Catholic University   

  roar_organisation_home_page roar_location_country roar_location_city  \
7      http://ucu.edu.ua/eng/                    ua               Lviv   

  roar_location_latitude roar_location_longitude roar_software  roar_geoname  \
7                    NaN                     NaN        dspace  geoname_2_UA   

  roar_version                                      roar_subjects  \
7        other  [BL, L1, D901, D204, H1, AC, BF, B1, BS, DK, H...   

             roar_date roar_note roar_suggestions roar_activity_low  \
7  2015-07-07 12:38:37       NaN              NaN               NaN   

  roar_activity_medium roar_activity_high roar_recordcount roar_recordhistory  \
7                  NaN                NaN              NaN                NaN   

  roar_fulltexts_total roar_fulltexts_docs roar_fulltexts_rtotal  \
7                  NaN                 NaN                   NaN   

  roar_fulltexts_rdocs     roar_registry_name roar_registry_id roar_submit_to  \
7                  NaN  [opendoar, celestial]     [5883, 3410]            NaN   

  roar_submitted_to_name roar_submitted_to_done roar_webometrics_rank  \
7                    NaN                    NaN                   NaN   

  roar_webometrics_size roar_webometrics_visibility  \
7                   NaN                         NaN   

  roar_webometrics_rich_files roar_webometrics_scholar roar_monthly_deposits  \
7                         NaN                      NaN                   NaN   

  roar_total_deposits             roar_association roar_unique_id  
7                 NaN  [ivy_league, russell_group]     roar_10013

# Joining information

In [7]:
dup = pd.read_csv('../data/interim/datasources_dedup_result_v2.csv', sep=';', quotechar='"', header=None, names=['dedup_id', 'duplicate_id', 'original_id', 'name', 'source'])
dup['unique_id'] = dup.source + '_' + dup.original_id
dup.head()

dedup_id  \
0  dedup::860320be12a1c050cd7731794e231bd3   
1  dedup::1aa7a8773e6a7fdacbcedf9999009a38   
2  dedup::31bceb0c3e2a260593e1e36655ebcee4   
3  dedup::e37b08dd3015330dcbb5d6663667b8b8   
4  dedup::2841194266115ac1cc04d19630cde46b   

                                     duplicate_id   original_id  \
0  opendoar____::2290a7385ed77cc5592dc2153229f082          1064   
1  opendoar____::191f8f858acda435ae0daf994e2a72c2          8648   
2  opendoar____::d5776aeecb3c45ab15adce6f5cb355f3          9713   
3  opendoar____::18997733ec258a9fcaf239cc55d53363           427   
4  re3data_____::3afbb2b45a3dd218a5a091ca773cf6c5  r3d100011189   

                                                name    source  \
0                 oxford university research archive  OpenDOAR   
1                   digital commons@georgia southern  OpenDOAR   
2                          materials data repository  OpenDOAR   
3   digital repository at the university of maryland  OpenDOAR   
4  PRISM: University of Calgary's Digital Repository   re3data   

              unique_id  
0         OpenDOAR_1064  
1         OpenDOAR_8648  
2         OpenDOAR_9713  
3          OpenDOAR_427  
4  re3data_r3d100011189

In [8]:
dup.describe()

dedup_id  \
count                                      4611   
unique                                     2188   
top     dedup::83d3d4b6c9579515e1679aca8cbc8033   
freq                                          5   

                                          duplicate_id original_id  \
count                                             4611        4611   
unique                                            4611        4155   
top     opendoar____::2290a7385ed77cc5592dc2153229f082        3089   
freq                                                 1           3   

                        name source      unique_id  
count                   4611   4611           4611  
unique                  3964      4           4611  
top     UPN JATIM REPOSITORY   roar  OpenDOAR_1064  
freq                       4   1977              1

In [9]:
dup = dup.merge(fairsharing_df, left_on='unique_id', right_on='FAIRsharing_unique_id', how='left')
dup = dup.merge(re3data_df, left_on='unique_id', right_on='re3data_unique_id', how='left')
dup = dup.merge(opendoar_df, left_on='unique_id', right_on='OpenDOAR_unique_id', how='left')
dup = dup.merge(roar_df, left_on='unique_id', right_on='roar_unique_id', how='left')
dup.head()

dedup_id  \
0  dedup::860320be12a1c050cd7731794e231bd3   
1  dedup::1aa7a8773e6a7fdacbcedf9999009a38   
2  dedup::31bceb0c3e2a260593e1e36655ebcee4   
3  dedup::e37b08dd3015330dcbb5d6663667b8b8   
4  dedup::2841194266115ac1cc04d19630cde46b   

                                     duplicate_id   original_id  \
0  opendoar____::2290a7385ed77cc5592dc2153229f082          1064   
1  opendoar____::191f8f858acda435ae0daf994e2a72c2          8648   
2  opendoar____::d5776aeecb3c45ab15adce6f5cb355f3          9713   
3  opendoar____::18997733ec258a9fcaf239cc55d53363           427   
4  re3data_____::3afbb2b45a3dd218a5a091ca773cf6c5  r3d100011189   

                                                name    source  \
0                 oxford university research archive  OpenDOAR   
1                   digital commons@georgia southern  OpenDOAR   
2                          materials data repository  OpenDOAR   
3   digital repository at the university of maryland  OpenDOAR   
4  PRISM: University of Calgary's Digital Repository   re3data   

              unique_id FAIRsharing_id FAIRsharing_type  \
0         OpenDOAR_1064            NaN              NaN   
1         OpenDOAR_8648            NaN              NaN   
2         OpenDOAR_9713            NaN              NaN   
3          OpenDOAR_427            NaN              NaN   
4  re3data_r3d100011189            NaN              NaN   

  FAIRsharing_attributes.created-at FAIRsharing_attributes.updated-at  \
0                               NaN                               NaN   
1                               NaN                               NaN   
2                               NaN                               NaN   
3                               NaN                               NaN   
4                               NaN                               NaN   

  FAIRsharing_attributes.metadata.doi FAIRsharing_attributes.metadata.name  \
0                                 NaN                                  NaN   
1                                 NaN                                  NaN   
2                                 NaN                                  NaN   
3                                 NaN                                  NaN   
4                                 NaN                                  NaN   

  FAIRsharing_attributes.metadata.status  \
0                                    NaN   
1                                    NaN   
2                                    NaN   
3                                    NaN   
4                                    NaN   

  FAIRsharing_attributes.metadata.contacts  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

  FAIRsharing_attributes.metadata.homepage  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   

   FAIRsharing_attributes.metadata.identifier  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  FAIRsharing_attributes.metadata.description  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  FAIRsharing_attributes.metadata.support-links  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                             

In [10]:
dup = dup.groupby('dedup_id').aggregate(list)
dup['source_set'] = dup.source.map(set)
dup.head()

<ipython-input-10-85e2703cd177>:2: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider using pd.concat instead.  To get a de-fragmented frame, use `newframe = frame.copy()`



duplicate_id  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de                                       [4612, 4649]   
dedup::001e6d882e54c780ce269d3c46997287  [re3data_____::4af9fe2bb93511a5e0f0c39e94d6557...   
dedup::0023a1e3447fdb31836536cc903f1310  [opendoar____::c6f798b844366ccd65d99bc7f31e0e0...   
dedup::003ab6b40af9b488decea7c582d150a2  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0064f599ed0adb5870a5b3ffe438e485  [16034, opendoar____::d1f157379ea7e51d4a8c07af...   

                                                  original_id  \
dedup_id                                                        
dedup::000871c1fc726f0b52dc86a4eeb027de          [4612, 4649]   
dedup::001e6d882e54c780ce269d3c46997287  [r3d100011306, 2094]   
dedup::0023a1e3447fdb31836536cc903f1310         [3410, 10013]   
dedup::003ab6b40af9b488decea7c582d150a2  [2315, r3d100011894]   
dedup::0064f599ed0adb5870a5b3ffe438e485         [16034, 9647]   

                                                                                      name  \
dedup_id                                                                                     
dedup::000871c1fc726f0b52dc86a4eeb027de  [IIT Bombay Institutional Repository, IIT Bomb...   
dedup::001e6d882e54c780ce269d3c46997287  [RESID Database of Protein Modifications, RESI...   
dedup::0023a1e3447fdb31836536cc903f1310  [erucu: electronic repository of the ukrainian...   
dedup::003ab6b40af9b488decea7c582d150a2                                 [Synapse, Synapse]   
dedup::0064f599ed0adb5870a5b3ffe438e485  [Giresun University Institutional Repository, ...   

                                                         source  \
dedup_id                                                          
dedup::000871c1fc726f0b52dc86a4eeb027de            [roar, roar]   
dedup::001e6d882e54c780ce269d3c46997287  [re3data, FAIRsharing]   
dedup::0023a1e3447fdb31836536cc903f1310        [OpenDOAR, roar]   
dedup::003ab6b40af9b488decea7c582d150a2  [FAIRsharing, re3data]   
dedup::0064f599ed0adb5870a5b3ffe438e485        [roar, OpenDOAR]   

                                                                        unique_id  \
dedup_id                                                                            
dedup::000871c1fc726f0b52dc86a4eeb027de                    [roar_4612, roar_4649]   
dedup::001e6d882e54c780ce269d3c46997287  [re3data_r3d100011306, FAIRsharing_2094]   
dedup::0023a1e3447fdb31836536cc903f1310               [OpenDOAR_3410, roar_10013]   
dedup::003ab6b40af9b488decea7c582d150a2  [FAIRsharing_2315, re3data_r3d100011894]   
dedup::0064f599ed0adb5870a5b3ffe438e485               [roar_16034, OpenDOAR_9647]   

                                        FAIRsharing_id  \
dedup_id                                                 
dedup::000871c1fc726f0b52dc86a4eeb027de     [nan, nan]   
dedup::001e6d882e54c780ce269d3c46997287    [nan, 2094]   
dedup::0023a1e3447fdb31836536cc903f1310     [nan, nan]   
dedup::003ab6b40af9b488decea7c582d150a2    [2315, nan]   
dedup::0064f599ed0adb5870a5b3ffe438e485     [nan, nan]   

                                                   FAIRsharing_type  \
dedup_id                                                              
dedup::000871c1fc726f0b52dc86a4eeb027de                  [nan, nan]   
dedup::001e6d882e54c780ce269d3c46997287  [nan, fairsharing-records]   
dedup::0023a1e3447fdb31836536cc903f1310                  [nan, nan]   
dedup::003ab6b40af9b488decea7c582d150a2  [fairsharing-records, nan]   
dedup::0064f599ed0adb5870a5b3ffe438e485                  [nan, nan]   

                                        FAIRsharing_attributes.created-at  \
dedup_id                                                                    
dedup::000871c1fc726f0b52dc86a4eeb027de                        [nan, nan]   
dedup::001e6d882e54c780ce269d3c46997287   [nan, 2014-11-04T15:23:40.000Z]   
dedup::0023a1e3447fdb3183

In [11]:
dup[dup.source_set.str.len() >= 2]

duplicate_id  \
dedup_id                                                                                     
dedup::001e6d882e54c780ce269d3c46997287  [re3data_____::4af9fe2bb93511a5e0f0c39e94d6557...   
dedup::0023a1e3447fdb31836536cc903f1310  [opendoar____::c6f798b844366ccd65d99bc7f31e0e0...   
dedup::003ab6b40af9b488decea7c582d150a2  [https://fairsharing.org/10.25504/FAIRsharing....   
dedup::0064f599ed0adb5870a5b3ffe438e485  [16034, opendoar____::d1f157379ea7e51d4a8c07af...   
dedup::00ac8ed3b4327bdd4ebbebcb2ba10a00  [610, opendoar____::299fb2142d7de959380f91c01c...   
...                                                                                    ...   
dedup::ff42b03a06a1bed4e936f0e04958e168  [7550, opendoar____::b4944963b5c83d545c3d3022b...   
dedup::ff49cc40a8890e6a60f40ff3026d2730  [1333, opendoar____::2bd7f907b7f5b6bbd91822c0c...   
dedup::ff4d70de478038c72282b7e4af1d4260  [opendoar____::95a0810a93a87065bf7b28490817e9e...   
dedup::ffbd6cbb019a1413183c8d08f2929307  [3108, opendoar____::ff7d0f525b3be596a51fb9194...   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98  [1126, opendoar____::443cb001c138b2561a0d90720...   

                                                  original_id  \
dedup_id                                                        
dedup::001e6d882e54c780ce269d3c46997287  [r3d100011306, 2094]   
dedup::0023a1e3447fdb31836536cc903f1310         [3410, 10013]   
dedup::003ab6b40af9b488decea7c582d150a2  [2315, r3d100011894]   
dedup::0064f599ed0adb5870a5b3ffe438e485         [16034, 9647]   
dedup::00ac8ed3b4327bdd4ebbebcb2ba10a00           [610, 1426]   
...                                                       ...   
dedup::ff42b03a06a1bed4e936f0e04958e168          [7550, 2890]   
dedup::ff49cc40a8890e6a60f40ff3026d2730          [1333, 1389]   
dedup::ff4d70de478038c72282b7e4af1d4260         [9752, 16367]   
dedup::ffbd6cbb019a1413183c8d08f2929307          [3108, 1912]   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98           [1126, 648]   

                                                                                      name  \
dedup_id                                                                                     
dedup::001e6d882e54c780ce269d3c46997287  [RESID Database of Protein Modifications, RESI...   
dedup::0023a1e3447fdb31836536cc903f1310  [erucu: electronic repository of the ukrainian...   
dedup::003ab6b40af9b488decea7c582d150a2                                 [Synapse, Synapse]   
dedup::0064f599ed0adb5870a5b3ffe438e485  [Giresun University Institutional Repository, ...   
dedup::00ac8ed3b4327bdd4ebbebcb2ba10a00                                 [Hedatuz, hedatuz]   
...                                                                                    ...   
dedup::ff42b03a06a1bed4e936f0e04958e168  [The Parthenon Frieze Repository, the partheno...   
dedup::ff49cc40a8890e6a60f40ff3026d2730                     [UnissResearch, unissresearch]   
dedup::ff4d70de478038c72282b7e4af1d4260  [european xfel publication database, European ...   
dedup::ffbd6cbb019a1413183c8d08f2929307  [Fotografía Sobre España en el Siglo XIX, foto...   
dedup::ffeed84c7cb1ae7bf4ec4bd78275bb98  [RIT Digital Media Library, rit digital media ...   

                                                         source  \
dedup_id                                                          
dedup::001e6d882e54c780ce269d3c46997287  [re3data, FAIRsharing]   
dedup::0023a1e3447fdb31836536cc903f1310        [OpenDOAR, roar]   
dedup::003ab6b40af9b488decea7c582d150a2  [FAIRsharing, re3data]   
dedup::0064f599ed0adb5870a5b3ffe438e485        [roar, OpenDOAR]   
dedup::00ac8ed3b4327bdd4ebbebcb2ba10a00        [roar, OpenDOAR]   
...                                                         ...   
dedup::ff42b03a06a1bed4e936f0e04958e168        [roar, OpenDOAR]   
dedup::ff49cc40a8890e6a60f40ff3026d2730        [roar, OpenDOAR]   
dedup::ff4d70de478038c72282b7e4af1d4260        [OpenDOAR, roar]   
dedup::ffbd6cbb019a1413183c8d08f2929307        [r